In [1]:
%matplotlib inline
import matplotlib.pyplot as plt
from sklearn.datasets import load_iris
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import train_test_split
import pandas as pd
import numpy as np
from sklearn import tree
import os
from sklearn import preprocessing

**First Table - Predicted Archive Type, classVar = proxyObsType** 

In [2]:
input_df = pd.read_csv('master_lipd.csv')

In [3]:
input_df.head()

dataset name compilation name     archiveType  \
0      117_723A.Godad.2011.lpd     Temp12k1_0_1  MarineSediment   
1     161_976.Martrat.2014.lpd     Temp12k1_0_1  MarineSediment   
2   165_1002C.Herbert.2000.lpd     Temp12k1_0_1  MarineSediment   
3   165_1002C.Herbert.2000.lpd     Temp12k1_0_1  MarineSediment   
4  Agassiz.Lecavalier.2017.lpd     Temp12k1_0_1      GlacierIce   

  predicted archiveType         TSid variableType       variableName  \
0        MarineSediment  Rwjoz3Y1iEf     measured      planktic.d18O   
1        MarineSediment  RFPqL4xjYcE     measured  C37.concentration   
2        MarineSediment  RYfbsh7Nj6W     measured               Uk37   
3        MarineSediment  RHba3kNQVGO     measured  C37.concentration   
4            GlacierIce  WEB623c3552     measured               melt   

      predicted proxyObsType remainder(variableName) proxyObservationType  \
0                       d18O               planktic.                  NaN   
1  37:2AlkenoneConcentration                     NaN                  NaN   
2                       Uk37                     NaN                  NaN   
3  37:2AlkenoneConcentration                     NaN                  NaN   
4                       Melt                     NaN             ice melt   

            final proxyValue  proxyValue from    units  hasProxySystem  \
0                       d18O                2   permil             NaN   
1  37:2AlkenoneConcentration                2        g             NaN   
2                       Uk37                2      NaN             NaN   
3  37:2AlkenoneConcentration                2        g             NaN   
4                   ice melt                1  percent             NaN   

   ProxySystem.SensorType interpretation/variable  \
0                     NaN                     NaN   
1                     NaN                     NaN   
2                     NaN                     NaN   
3                     NaN                     NaN   
4                     NaN                       T   

  interpretation/variableDetail  
0                           NaN  
1                           NaN  
2                           NaN  
3                           NaN  
4                           NaN

In [5]:
first_df = input_df[['predicted archiveType', 'final proxyValue']]
print(first_df.head())
print(first_df.shape)
print(first_df.index)

  predicted archiveType           final proxyValue
0        MarineSediment                       d18O
1        MarineSediment  37:2AlkenoneConcentration
2        MarineSediment                       Uk37
3        MarineSediment  37:2AlkenoneConcentration
4            GlacierIce                   ice melt
(3723, 2)
RangeIndex(start=0, stop=3723, step=1)


In [6]:
import collections
def get_counter_archive(list_val):
    counter_archive = collections.Counter(list_val)
    counter_archive = {key:value for key,value in dict(counter_archive).items() if value > 10}
    return counter_archive

In [7]:
counter_archive = get_counter_archive(first_df['predicted archiveType'])
counter_archive

{'MarineSediment': 1079,
 'GlacierIce': 283,
 'LakeSediment': 192,
 'Speleothem': 65,
 'Midden': 27,
 'Coral': 193,
 'Wood': 1845}

Removing all the proxyObservationTypes that appear only once as they do not contribute much to the system.
Apart from that remove the following values:
1. 'latitude sample'
2. 'longitude sample' 
3. 'elevation sample'
4. 'Notes'
5. 'Composite'

In [8]:
def get_counter_proxy(list_val):
    counter_proxy = collections.Counter(list_val)

    cleaned_proxy = {key:value for key,value in dict(counter_proxy).items() if value > 1}
    del cleaned_proxy['latitude sample']
    del cleaned_proxy['longitude sample']
    del cleaned_proxy['elevation sample']
    del cleaned_proxy['Notes']
    del cleaned_proxy['Composite']
    discard_set = set(counter_proxy.keys()).difference(set(cleaned_proxy.keys()))
    return cleaned_proxy, discard_set

In [9]:
counter_proxy, discard_set = get_counter_proxy(first_df['final proxyValue'])

In [11]:
len(counter_proxy)

52

In [12]:
# removing all the values from the discard set
other_flag = False
first_df = first_df[~first_df['final proxyValue'].isin(discard_set)]

# replacing values from discard set as class = 'other'
# other_flag = True
# first_df = first_df.replace(list(discard_set), 'other')
first_df.shape

if other_flag:
    counter_proxy['other'] = 0

In [13]:
first_df.head(10)

predicted archiveType           final proxyValue
0         MarineSediment                       d18O
1         MarineSediment  37:2AlkenoneConcentration
2         MarineSediment                       Uk37
3         MarineSediment  37:2AlkenoneConcentration
5           LakeSediment                       d18O
6             GlacierIce                       d18O
7              Ice-other                         dD
8              Ice-other                       d18O
9              Ice-other            deuteriumExcess
10             Ice-other                         dD

In [14]:
index_drop = first_df[(first_df['predicted archiveType'] != 'MarineSediment') & (first_df['predicted archiveType'] != 'GlacierIce') & (first_df['predicted archiveType'] != 'LakeSediment') & (first_df['predicted archiveType'] != 'Speleothem') & (first_df['predicted archiveType'] != 'Midden') & (first_df['predicted archiveType'] != 'Coral') & (first_df['predicted archiveType'] != 'Wood')].index

In [15]:
first_df.drop(index_drop, inplace = True)
first_df.head()

predicted archiveType           final proxyValue
0        MarineSediment                       d18O
1        MarineSediment  37:2AlkenoneConcentration
2        MarineSediment                       Uk37
3        MarineSediment  37:2AlkenoneConcentration
5          LakeSediment                       d18O

In [16]:
first_df.reset_index()

index predicted archiveType           final proxyValue
0         0        MarineSediment                       d18O
1         1        MarineSediment  37:2AlkenoneConcentration
2         2        MarineSediment                       Uk37
3         3        MarineSediment  37:2AlkenoneConcentration
4         5          LakeSediment                       d18O
...     ...                   ...                        ...
3589   3718            GlacierIce                         Na
3590   3719            GlacierIce                   ammonium
3591   3720            GlacierIce                          K
3592   3721            GlacierIce                         Mg
3593   3722            GlacierIce                         Ca

[3594 rows x 3 columns]

In [17]:
first_df.shape

(3594, 2)

In [18]:
import copy
temp_df = copy.deepcopy(first_df)

In [19]:
first_df = copy.deepcopy(temp_df)

In [20]:
first_df.to_csv('archive_vs_proxy.csv')

In [21]:
# FEATURE ENCODING ARCHIVE TYPE 

predicted_archive_type_encode = {tup[0]:i for i, tup in enumerate(sorted(counter_archive.items(), key= lambda input : (-input[1], input[0])))}
predicted_archive_type_encode

{'Wood': 0,
 'MarineSediment': 1,
 'GlacierIce': 2,
 'Coral': 3,
 'LakeSediment': 4,
 'Speleothem': 5,
 'Midden': 6}

In [22]:
# FEATURE ENCODING PROXY OBS TYPE
final_proxy_val_encode = {tup[0]:i for i, tup in enumerate(sorted(counter_proxy.items(), key= lambda input : (-input[1], input[0])))}
final_proxy_val_encode

{'d18O': 0,
 'Trsgi': 1,
 'd13C': 2,
 'Core': 3,
 'SE': 4,
 'sampleCount': 5,
 'ARS': 6,
 'Corrs': 7,
 'EPS': 8,
 'RBar': 9,
 'Residual': 10,
 'SD': 11,
 'Segment': 12,
 'ringWidth': 13,
 'dD': 14,
 'Mg/Ca': 15,
 'CaCO3': 16,
 'TOC': 17,
 'Uk37': 18,
 'planktonic.foram.abundance': 19,
 'calcification': 20,
 'Sr/Ca': 21,
 'IRD': 22,
 'BSi': 23,
 'DBD': 24,
 '37:2AlkenoneConcentration': 25,
 'deuteriumExcess': 26,
 'thickness': 27,
 'Density': 28,
 'MXD': 29,
 'TEX86': 30,
 'benthic.d13C.error': 31,
 'benthic.d18O.error': 32,
 'brGDGT': 33,
 'dust': 34,
 'nitrate': 35,
 'sulfate': 36,
 'BIT': 37,
 'Na': 38,
 'C/N': 39,
 'Ca': 40,
 'Cl': 41,
 'F': 42,
 'K': 43,
 'Mg': 44,
 'R570_630': 45,
 'R660_670': 46,
 'ammonium': 47,
 'chloride': 48,
 'melt': 49,
 'planktonic.d13C.error': 50,
 'sampleID': 51}

In [20]:
# SKIPPED
first_df['final proxyValue'] = first_df['final proxyValue'].astype('category')

In [382]:
# SKIPPED
first_df['final proxyValue'] = first_df['final proxyValue'].astype('category')
first_df['final proxyValue'] = first_df['final proxyValue'].cat.codes.astype('category')
first_df

predicted archiveType final proxyValue
0           MarineSediment               75
1           MarineSediment                0
2           MarineSediment               54
3           MarineSediment                0
4               GlacierIce               83
...                    ...              ...
3718            GlacierIce               32
3719            GlacierIce               59
3720            GlacierIce               22
3721            GlacierIce               29
3722            GlacierIce                7

[3684 rows x 2 columns]

In [296]:
# SKIPPED

# from sklearn.compose import ColumnTransformer

# ct = ColumnTransformer([("predicted archiveType",preprocessing.OneHotEncoder(), [0])], remainder = 'passthrough')
# first_df = ct.fit_transform(first_df)

# first_df

ohe = preprocessing.OneHotEncoder()
archive_ohe = pd.get_dummies(first_df, columns=["predicted archiveType"], prefix=["Type"])
# archive_ohe = pd.DataFrame(ohe.fit_transform(first_df[['predicted archiveType']]).toarray())
first_df = first_df.merge(archive_ohe, left_index=True, right_index=True, how='inner')
# first_df['predicted archiveType'] = ohe.fit_transform(first_df['predicted archiveType'])
print(first_df.shape)
first_df.head()

(3684, 10)


predicted archiveType         final proxyValue_x         final proxyValue_y  \
0        MarineSediment                       d18O                       d18O   
1        MarineSediment  37:2AlkenoneConcentration  37:2AlkenoneConcentration   
2        MarineSediment                       Uk37                       Uk37   
3        MarineSediment  37:2AlkenoneConcentration  37:2AlkenoneConcentration   
4            GlacierIce                   ice melt                   ice melt   

   Type_Coral  Type_GlacierIce  Type_LakeSediment  Type_MarineSediment  \
0           0                0                  0                    1   
1           0                0                  0                    1   
2           0                0                  0                    1   
3           0                0                  0                    1   
4           0                1                  0                    0   

   Type_Midden  Type_Speleothem  Type_Wood  
0            0                0          0  
1            0                0          0  
2            0                0          0  
3            0                0          0  
4            0                0          0

In [23]:
encoded_data = {'predicted archiveType' : predicted_archive_type_encode, 'final proxyValue' : final_proxy_val_encode}

In [24]:
first_df.replace(encoded_data, inplace=True)

In [25]:
first_df.head()

predicted archiveType  final proxyValue
0                      1                 0
1                      1                25
2                      1                18
3                      1                25
5                      4                 0

In [26]:
X_train, X_test, Y_train, Y_test = train_test_split(first_df[['predicted archiveType']], first_df[['final proxyValue']], random_state=0)

# X_train = X_train.reshape(-1, 1)

print(X_train.shape)
print(X_test.shape)
print(Y_train.shape)
print(Y_test.shape)

(2695, 1)
(899, 1)
(2695, 1)
(899, 1)


In [27]:
# Limit max depth
model = RandomForestClassifier(max_depth = 10, n_estimators=10, max_features = None, oob_score=True)

# Train
model.fit(X_train, Y_train)

predictions_all = np.array([tree.predict(X_test) for tree in model.estimators_])
print(predictions_all.shape)
print(predictions_all)

(10, 899)
[[1. 0. 1. ... 1. 0. 1.]
 [1. 0. 1. ... 1. 0. 1.]
 [1. 0. 1. ... 1. 0. 1.]
 ...
 [1. 0. 1. ... 1. 0. 1.]
 [1. 0. 1. ... 1. 0. 1.]
 [1. 0. 1. ... 1. 0. 1.]]


<ipython-input-27-ce7cee163ed9>:5: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  model.fit(X_train, Y_train)
C:\Users\shrav\Miniconda3\envs\lipd\lib\site-packages\sklearn\ensemble\_forest.py:540: UserWarning: Some inputs do not have OOB scores. This probably means too few trees were used to compute any reliable oob estimates.
  warn("Some inputs do not have OOB scores. "
C:\Users\shrav\Miniconda3\envs\lipd\lib\site-packages\sklearn\ensemble\_forest.py:544: RuntimeWarning: invalid value encountered in true_divide
  decision = (predictions[k] /


In [28]:
estimator_limited = model.estimators_[5]
estimator_limited

DecisionTreeClassifier(max_depth=10, random_state=412068657)

In [29]:
fn = ['predicted archiveType']
cn = list(counter_proxy.keys())
from sklearn.tree import export_graphviz
export_graphviz(estimator_limited, out_file='tree_archive_proxy1.dot', feature_names=fn, class_names=cn,
                rounded = True, proportion = False, precision = 2, filled = True)

In [30]:
!dot -Tpng tree_archive_proxy1.dot -o tree_archive_proxy1.png -Gdpi=600

In [31]:
from IPython.display import Image
Image(filename = 'tree_archive_proxy1.png')

In [32]:
print(Y_test)

      final proxyValue
2233                 8
923                  0
1795                 1
3627                 0
623                  0
...                ...
1476                 0
1890                 1
1873                 1
3646                21
2916                 6

[899 rows x 1 columns]


In [33]:
# Make predictions on test data
predictions = model.predict(X_test)
predictions = predictions.reshape(-1, 1)
# Performance metrics
errors = abs(predictions - Y_test)
# print(errors)
print('Average absolute error:', round(np.mean(errors), 2), 'degrees.')

Average absolute error: final proxyValue    5.48
dtype: float64 degrees.


In [34]:
from sklearn.metrics import accuracy_score
accuracy_score(Y_test, predictions)

0.3704115684093437

In [35]:
from sklearn.metrics import confusion_matrix
confusion_matrix(Y_test, predictions)

array([[233,  19,   0, ...,   0,   0,   0],
       [  0, 100,   0, ...,   0,   0,   0],
       [ 85,   0,   0, ...,   0,   0,   0],
       ...,
       [  1,   0,   0, ...,   0,   0,   0],
       [  1,   0,   0, ...,   0,   0,   0],
       [  1,   0,   0, ...,   0,   0,   0]], dtype=int64)

In [36]:
# CALCUATING ACCURACY FOR EACH TREE
for i, tree in enumerate(model.estimators_):
    pred = tree.predict(X_test)
    pred = pred.reshape(-1, 1)
    print('Estimator: ', (i+1), 'Accuracy Score: ', + accuracy_score(Y_test, pred))

Estimator:  1 Accuracy Score:  0.3704115684093437
Estimator:  2 Accuracy Score:  0.3704115684093437
Estimator:  3 Accuracy Score:  0.3704115684093437
Estimator:  4 Accuracy Score:  0.3704115684093437
Estimator:  5 Accuracy Score:  0.3704115684093437
Estimator:  6 Accuracy Score:  0.3704115684093437
Estimator:  7 Accuracy Score:  0.3704115684093437
Estimator:  8 Accuracy Score:  0.3704115684093437
Estimator:  9 Accuracy Score:  0.3704115684093437
Estimator:  10 Accuracy Score:  0.3704115684093437


#### Setting a baseline using DummyClassifier

In [94]:
from sklearn.dummy import DummyClassifier

In [95]:
dummy_clf = DummyClassifier(strategy='stratified', random_state=42)

In [96]:
dummy_clf.fit(X_train, Y_train)

DummyClassifier(random_state=42, strategy='stratified')

In [97]:
dummy_clf.predict(X_test)

array([33,  0,  0, 33,  0, 44,  0, 48, 48, 32,  0,  0,  6, 35, 50, 46, 46,
        3, 33, 32, 22,  0, 35,  6,  5, 48,  0, 29, 43, 42, 46,  0, 46,  3,
       49, 49,  0, 47, 47,  9,  6,  0, 25, 32,  0,  0, 47, 48,  7, 48, 35,
       42, 49,  0, 32, 23, 47,  6, 50, 45,  6, 43, 32, 14, 11,  0,  6, 35,
        0,  0,  0,  6, 33, 35,  0,  0,  0, 49,  6,  0, 41,  0, 46, 51,  0,
       35,  0, 32, 48, 35,  0,  0,  6, 35, 49,  6,  2, 49, 43,  6, 35, 33,
       43, 46, 44, 35, 43, 32,  0,  0, 35, 32,  0, 29,  6, 48, 45, 46, 50,
        0,  3, 49, 49, 35,  0, 46, 48,  0,  0,  6, 35, 44, 30,  0,  0,  4,
       35,  0,  3,  0, 47,  0, 32,  0,  0, 44,  0, 33,  0, 39,  0, 35, 35,
       48, 33, 32, 43, 47, 44, 47,  9, 25, 33, 33, 43,  3, 46,  0, 32, 44,
        0, 47, 35, 46,  6,  0,  3, 25, 45, 32, 50,  0, 32, 35, 45, 25, 43,
       50, 46, 43,  6, 43, 43, 35,  0,  6, 49, 46, 35,  6, 42, 48, 22, 33,
        0,  6, 35,  0, 50, 35, 47, 32,  6,  0, 42,  0,  0, 46, 35,  6, 29,
        3,  0, 39, 47, 46

In [98]:
dummy_clf.score(X_test, Y_test)

0.13236929922135707

***Randomly ordering predicted archive type and proxy***

In [42]:
predicted_archive_type_random_encode = {tup[0]:i for i, tup in enumerate(counter_archive.items())}
predicted_archive_type_random_encode

{'MarineSediment': 0,
 'GlacierIce': 1,
 'LakeSediment': 2,
 'Speleothem': 3,
 'Midden': 4,
 'Coral': 5,
 'Wood': 6}

In [43]:
final_proxy_val_random_encode = {tup[0]:i for i, tup in enumerate(counter_proxy.items())}
final_proxy_val_random_encode

{'d18O': 0,
 '37:2AlkenoneConcentration': 1,
 'Uk37': 2,
 'dD': 3,
 'deuteriumExcess': 4,
 'Mg/Ca': 5,
 'd13C': 6,
 'TOC': 7,
 'C/N': 8,
 'DBD': 9,
 'CaCO3': 10,
 'TEX86': 11,
 'BIT': 12,
 'brGDGT': 13,
 'thickness': 14,
 'dust': 15,
 'F': 16,
 'Cl': 17,
 'sulfate': 18,
 'nitrate': 19,
 'Na': 20,
 'ammonium': 21,
 'K': 22,
 'Mg': 23,
 'Ca': 24,
 'Sr/Ca': 25,
 'IRD': 26,
 'benthic.d13C.error': 27,
 'benthic.d18O.error': 28,
 'planktonic.foram.abundance': 29,
 'BSi': 30,
 'planktonic.d13C.error': 31,
 'SE': 32,
 'Core': 33,
 'Density': 34,
 'Trsgi': 35,
 'MXD': 36,
 'melt': 37,
 'chloride': 38,
 'sampleID': 39,
 'R570_630': 40,
 'R660_670': 41,
 'sampleCount': 42,
 'Segment': 43,
 'ringWidth': 44,
 'Residual': 45,
 'ARS': 46,
 'Corrs': 47,
 'RBar': 48,
 'SD': 49,
 'EPS': 50,
 'calcification': 51}

In [44]:
encoded_data = {'predicted archiveType' : predicted_archive_type_random_encode, 'final proxyValue' : final_proxy_val_random_encode}

In [45]:
first_df = copy.deepcopy(temp_df)

In [46]:
first_df.replace(encoded_data, inplace=True)

In [47]:
X_train, X_test, Y_train, Y_test = train_test_split(first_df[['predicted archiveType']], first_df[['final proxyValue']], random_state=0)

# X_train = X_train.reshape(-1, 1)

print(X_train.shape)
print(X_test.shape)
print(Y_train.shape)
print(Y_test.shape)

(2695, 1)
(899, 1)
(2695, 1)
(899, 1)


In [48]:
# Limit max depth
model = RandomForestClassifier(max_depth = 10, n_estimators=10, max_features = None, oob_score=True)

# Train
model.fit(X_train, Y_train)

predictions_all = np.array([tree.predict(X_test) for tree in model.estimators_])
print(predictions_all.shape)
print(predictions_all)

(10, 899)
[[35.  0. 35. ... 35.  0. 35.]
 [35.  0. 35. ... 35.  0. 35.]
 [35.  0. 35. ... 35.  0. 35.]
 ...
 [35.  0. 35. ... 35.  0. 35.]
 [35.  0. 35. ... 35.  0. 35.]
 [35.  0. 35. ... 35.  0. 35.]]


<ipython-input-48-ce7cee163ed9>:5: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  model.fit(X_train, Y_train)
C:\Users\shrav\Miniconda3\envs\lipd\lib\site-packages\sklearn\ensemble\_forest.py:540: UserWarning: Some inputs do not have OOB scores. This probably means too few trees were used to compute any reliable oob estimates.
  warn("Some inputs do not have OOB scores. "
C:\Users\shrav\Miniconda3\envs\lipd\lib\site-packages\sklearn\ensemble\_forest.py:544: RuntimeWarning: invalid value encountered in true_divide
  decision = (predictions[k] /


In [49]:
estimator_limited = model.estimators_[5]
estimator_limited

DecisionTreeClassifier(max_depth=10, random_state=416822297)

In [50]:
fn = ['predicted archiveType']
cn = list(counter_proxy.keys())
from sklearn.tree import export_graphviz
export_graphviz(estimator_limited, out_file='tree_archive_proxy1.dot', feature_names=fn, class_names=cn,
                rounded = True, proportion = False, precision = 2, filled = True)

In [51]:
!dot -Tpng tree_archive_proxy1.dot -o tree_archive_proxy1.png -Gdpi=600

In [52]:
from IPython.display import Image
Image(filename = 'tree_archive_proxy1.png')

In [53]:

# CALCUATING ACCURACY FOR EACH TREE
for i, tree in enumerate(model.estimators_):
    pred = tree.predict(X_test)
    pred = pred.reshape(-1, 1)
    print('Estimator: ', (i+1), 'Accuracy Score: ', + accuracy_score(Y_test, pred))

Estimator:  1 Accuracy Score:  0.3704115684093437
Estimator:  2 Accuracy Score:  0.3704115684093437
Estimator:  3 Accuracy Score:  0.3704115684093437
Estimator:  4 Accuracy Score:  0.3704115684093437
Estimator:  5 Accuracy Score:  0.3704115684093437
Estimator:  6 Accuracy Score:  0.3704115684093437
Estimator:  7 Accuracy Score:  0.3704115684093437
Estimator:  8 Accuracy Score:  0.3704115684093437
Estimator:  9 Accuracy Score:  0.3704115684093437
Estimator:  10 Accuracy Score:  0.3704115684093437


**Second Table - ProxyObsType, classVar = units** 

In [54]:
second_df = input_df[['final proxyValue', 'units']]
second_df.shape

(3723, 2)

In [55]:
second_df.head()

final proxyValue    units
0                       d18O   permil
1  37:2AlkenoneConcentration        g
2                       Uk37      NaN
3  37:2AlkenoneConcentration        g
4                   ice melt  percent

In [56]:
# counter_archive = get_counter_archive(second_df['predicted archiveType'])
# counter_archive
counter_proxy, discard_set = get_counter_proxy(second_df['final proxyValue'])

In [57]:
second_df = second_df[~second_df['final proxyValue'].isin(discard_set)]

In [58]:
second_df.shape

(3631, 2)

In [59]:
# second_df = second_df[second_df['predicted archiveType'].isin(set(counter_archive.keys()))]
# second_df.head()

In [60]:
second_df.shape

(3631, 2)

In [61]:
second_df.to_csv('proxy_vs_units.csv')

In [62]:
second_df = pd.get_dummies(second_df, columns=['final proxyValue', 'units'])

In [63]:
second_df.head()
second_df.to_csv('df_to_csv.csv')

In [99]:
#second_df = second_df.replace(np.nan, 'no units', regex=True)
#count_class = collections.Counter(second_df['units'])


In [64]:
fn = second_df.iloc[:, 0:52].values
fn
cn = second_df.iloc[:, 52:].values

In [65]:
X_train_u, X_test_u, Y_train_u, Y_test_u = train_test_split(fn, cn, random_state=0)

# X_train = X_train.reshape(-1, 1)

print(X_train_u.shape)
print(X_test_u.shape)
print(Y_train_u.shape)
print(Y_test_u.shape)

(2723, 52)
(908, 52)
(2723, 26)
(908, 26)


In [82]:
# Limit max depth
model_units = RandomForestClassifier(max_depth = None, n_estimators=10, max_features = None, oob_score=True)

# Train
model_units.fit(X_train_u, Y_train_u)

predictions_all = np.array([tree.predict(X_test_u) for tree in model_units.estimators_])
print(predictions_all.shape)
print(predictions_all)

(10, 908, 26)
[[[0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  ...
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]]

 [[0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  ...
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]]

 [[0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  ...
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]]

 ...

 [[0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  ...
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]]

 [[0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  ...
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]]

 [[0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  ...
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.]
  [0. 0. 0. ... 0. 0. 0.

C:\Users\shrav\Miniconda3\envs\lipd\lib\site-packages\sklearn\ensemble\_forest.py:540: UserWarning: Some inputs do not have OOB scores. This probably means too few trees were used to compute any reliable oob estimates.
  warn("Some inputs do not have OOB scores. "
C:\Users\shrav\Miniconda3\envs\lipd\lib\site-packages\sklearn\ensemble\_forest.py:544: RuntimeWarning: invalid value encountered in true_divide
  decision = (predictions[k] /


In [83]:
estimator_units = model_units.estimators_[5]
estimator_units

DecisionTreeClassifier(random_state=1813106807)

In [84]:
from sklearn import tree
text_representation = tree.export_text(model_units.estimators_[5])
print(text_representation)

|--- feature_39 <= 0.50
|   |--- feature_38 <= 0.50
|   |   |--- feature_48 <= 0.50
|   |   |   |--- feature_47 <= 0.50
|   |   |   |   |--- feature_40 <= 0.50
|   |   |   |   |   |--- feature_18 <= 0.50
|   |   |   |   |   |   |--- feature_6 <= 0.50
|   |   |   |   |   |   |   |--- feature_29 <= 0.50
|   |   |   |   |   |   |   |   |--- feature_36 <= 0.50
|   |   |   |   |   |   |   |   |   |--- feature_10 <= 0.50
|   |   |   |   |   |   |   |   |   |   |--- feature_14 <= 0.50
|   |   |   |   |   |   |   |   |   |   |   |--- truncated branch of depth 25
|   |   |   |   |   |   |   |   |   |   |--- feature_14 >  0.50
|   |   |   |   |   |   |   |   |   |   |   |--- class: 0
|   |   |   |   |   |   |   |   |   |--- feature_10 >  0.50
|   |   |   |   |   |   |   |   |   |   |--- class: 0
|   |   |   |   |   |   |   |   |--- feature_36 >  0.50
|   |   |   |   |   |   |   |   |   |--- class: 0
|   |   |   |   |   |   |   |--- feature_29 >  0.50
|   |   |   |   |   |   |   |   |--- class: 0

In [85]:
fn = list(second_df.columns)
fn = fn[:52]
print(fn)
print(len(fn))
cn = list(second_df.columns)
cn = cn[52:]
# cn = model_units.classes_
print(cn)
print(len(cn))
from sklearn.tree import export_graphviz
export_graphviz(estimator_units, out_file='tree_for_units.dot', feature_names=fn, class_names=cn,
                rounded = True, proportion = False, precision = 2, filled = True)

['final proxyValue_37:2AlkenoneConcentration', 'final proxyValue_ARS', 'final proxyValue_BIT', 'final proxyValue_BSi', 'final proxyValue_C/N', 'final proxyValue_Ca', 'final proxyValue_CaCO3', 'final proxyValue_Cl', 'final proxyValue_Core', 'final proxyValue_Corrs', 'final proxyValue_DBD', 'final proxyValue_Density', 'final proxyValue_EPS', 'final proxyValue_F', 'final proxyValue_IRD', 'final proxyValue_K', 'final proxyValue_MXD', 'final proxyValue_Mg', 'final proxyValue_Mg/Ca', 'final proxyValue_Na', 'final proxyValue_R570_630', 'final proxyValue_R660_670', 'final proxyValue_RBar', 'final proxyValue_Residual', 'final proxyValue_SD', 'final proxyValue_SE', 'final proxyValue_Segment', 'final proxyValue_Sr/Ca', 'final proxyValue_TEX86', 'final proxyValue_TOC', 'final proxyValue_Trsgi', 'final proxyValue_Uk37', 'final proxyValue_ammonium', 'final proxyValue_benthic.d13C.error', 'final proxyValue_benthic.d18O.error', 'final proxyValue_brGDGT', 'final proxyValue_calcification', 'final proxyV

In [86]:
!dot -Tpng tree_for_units.dot -o tree_for_units.png 

In [87]:
from IPython.display import Image
Image(filename='tree_for_units.png')

In [88]:
# CALCUATING ACCURACY FOR EACH TREE
for i, tree in enumerate(model_units.estimators_):
    pred = tree.predict(X_test_u)
#     pred = pred.reshape(-1, 1)
#     print(pred, Y_test_u)
    print('Estimator: ', (i+1), 'Accuracy Score: ', + accuracy_score(Y_test_u, pred))

Estimator:  1 Accuracy Score:  0.8612334801762115
Estimator:  2 Accuracy Score:  0.8623348017621145
Estimator:  3 Accuracy Score:  0.8557268722466961
Estimator:  4 Accuracy Score:  0.8601321585903083
Estimator:  5 Accuracy Score:  0.8601321585903083
Estimator:  6 Accuracy Score:  0.8612334801762115
Estimator:  7 Accuracy Score:  0.8645374449339207
Estimator:  8 Accuracy Score:  0.8601321585903083
Estimator:  9 Accuracy Score:  0.8623348017621145
Estimator:  10 Accuracy Score:  0.8634361233480177


In [89]:
from sklearn.dummy import DummyClassifier

In [90]:
dummy_clf = DummyClassifier(strategy="stratified", random_state=42)

In [91]:
dummy_clf.fit(X_train_u, Y_train_u)

DummyClassifier(random_state=42, strategy='stratified')

In [92]:
dummy_clf.predict(X_test_u)

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 1, 0, ..., 0, 0, 0]], dtype=uint8)

In [93]:
dummy_clf.score(X_test_u, Y_test_u)

0.2786343612334802